In [1]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from ParticleSwarm import ParticleSwarmOptimization, GenerationSnapshot, Particle

# Create the map with randomly generated houses

In [2]:
Dimensions = (0,200,0,200)
NHouses = 70

In [3]:
Swarm = ParticleSwarmOptimization(NHouses, Dimensions)

## Calculate X Particles for Y Generations

In [4]:
NParticles = 10
NGenerations = 120

In [5]:
gens : list = Swarm.calculate(NParticles, NGenerations)

# Create a function to create animation of the particles moving

In [6]:
from random import random

def evaluateCoord(X, Y, Houses:list[Particle]):
    sum = 0
    for house in Houses:
        sum += ParticleSwarmOptimization.evaluateCoords(X,Y,house.getX(),house.getY())
    return sum

def animate_snapshots(snapshots:list[GenerationSnapshot], interval=200):
    fig, ax = plt.subplots(figsize=(7,7))

    margin = 12
    DimensionsR = (Dimensions[0]-margin, Dimensions[1]+margin, Dimensions[2]-margin , Dimensions[3]+margin)
    ax.set_xlim(DimensionsR[0], DimensionsR[1])
    ax.set_ylim(DimensionsR[2], DimensionsR[3])

    X, Y = np.meshgrid(np.linspace(DimensionsR[0], DimensionsR[1], 256), np.linspace(DimensionsR[2], DimensionsR[3], 256))
    Z = evaluateCoord(X,Y,Swarm.getHouses())
    levels = np.linspace(Z.min(), Z.max(), 25)
    ax.contourf(X, Y, Z, levels=levels, cmap='Greens')

    # House scatter
    house_scatter = ax.scatter([], [], c='red', marker='s', label='Houses')
    # Particle scatter
    particle_scatter = ax.scatter([], [], c='blue', marker='o', label='Particles')

    # Initialize quiver with first snapshot
    snap0 = snapshots[0]
    px0 = np.array([p.getPosition().getX() for p in snap0.particles])
    py0 = np.array([p.getPosition().getY() for p in snap0.particles])
    vx0 = np.array([p.getVelocity().getX() for p in snap0.particles])
    vy0 = np.array([p.getVelocity().getY() for p in snap0.particles])
    quiver = ax.quiver(px0, py0, vx0, vy0, angles='xy', scale_units='xy', scale=1, color='green')

    best_scatter = ax.scatter([], [], c='yellow', marker='*', label='Best')

    ax.set_xlabel("X")
    ax.set_ylabel("Y")
    ax.grid(True)
    ax.axis('equal')
    ax.legend()



    # ---------------- UPDATE FUNCTION ----------------
    def update(i):
        snap : GenerationSnapshot = snapshots[i]

        # Particle positions
        ps = [[p.getPosition().getX(), p.getPosition().getY()] for p in snap.particles]

        # Particle velocities
        vx = np.array([p.getVelocity().getX() for p in snap.particles])
        vy = np.array([p.getVelocity().getY() for p in snap.particles])

        # House positions
        hx = np.array([h.getPosition().getX() for h in snap.houses])
        hy = np.array([h.getPosition().getY() for h in snap.houses])

        # Update scatters
        house_scatter.set_offsets(np.c_[hx, hy])
        particle_scatter.set_offsets(ps)

        if (snap.best):
            best_scatter.set_offsets([snap.best.position.x, snap.best.position.y])
        else:
            best_scatter.set_offsets([])

        # Update quiver arrows
        quiver.set_offsets(ps)
        quiver.set_UVC(vx, vy)

        ax.set_title(f"Generation {snap.gennum}")
        return house_scatter, particle_scatter, quiver, best_scatter

    anim = FuncAnimation(
        fig,
        update,
        frames=len(snapshots),
        interval=interval,
        blit=False
    )

    plt.close(fig)
    return anim


# Display animation

In [7]:
from IPython.display import HTML
anim = animate_snapshots(gens, interval=100)
HTML(anim.to_jshtml())

## Save animation

In [8]:
from random import randint
anim.save(f"../media/example{randint(1000, 9999)}.gif")

MovieWriter ffmpeg unavailable; using Pillow instead.
